In [2]:
#Ｉmport necessary packages
import torch
import torch.nn as nn
import numpy as np
from matplotlib import pyplot as plt
import xitorch
from xitorch.optimize import rootfinder
import optuna
from torch.utils.data import TensorDataset, DataLoader
import joblib 

# Memory management on GPU
import gc

# Import time
import time

# Testify whether GPU is available
print("Cuda is available: ", torch.cuda.is_available())
device = torch.device("cuda:0" if torch.cuda.is_available() else "cpu")
# device = "cpu"
print("Device is: ", device)

def memory_stats():
    print("Memory allocated: ", torch.cuda.memory_allocated()/1024**2)
    print("Memory cached: ", torch.cuda.memory_reserved()/1024**2)
memory_stats()


Cuda is available:  True
Device is:  cuda:0
Memory allocated:  0.0
Memory cached:  0.0


In [3]:
# Define MLP for potentials
class PP(nn.Module):
    # Constructor
    def __init__(self, NNs, input_dim = 1, output_dim = 1):
        super().__init__()
        self.fc = nn.Sequential(
            nn.Linear(input_dim, NNs[0]), 
            nn.ELU(),
        )
        
        for i in range(len(NNs) - 1):
            self.fc.append(nn.Linear(NNs[i], NNs[i + 1]))
            self.fc.append(nn.ELU())
        
        self.fc.append(nn.Linear(NNs[-1], output_dim))
    
    # Forward function
    def forward(self, x):
        return self.fc(x)

# Data generation

In [4]:
from DataGeneration import generateSamples, genVVtt
import os

generating_flag = False
kwgs = {
    "beta" : [0.011, 0.016, 1. / 1.e1, 0.58], 
    "totalNofSeqs" : 1024 * 16, 
    "NofIntervalsRange" : [5, 11], 
    "VVRange" : [-10, 3], 
    "VVLenRange" : [8, 9], 
    "theta0" : 1., 
    "prefix" : "Trial1003", 
    "NofVVSteps" : 400, 
}

# Generate / load data
dataFile = "./data/" + kwgs["prefix"] + ".pt"

if generating_flag or not(os.path.isfile(dataFile)):
    print("Generating data")
    generateSamples(kwgs)

shit = torch.load(dataFile)
Vs = shit["Vs"]
thetas = shit["thetas"]
fs = shit["fs"]

# Stack data as
Vs = torch.stack(Vs)[:1000, :500]
thetas = torch.stack(thetas)[:1000, :500]
fs = torch.stack(fs)[:1000, :500]
ts = shit["ts"][:1000, :500]

In [5]:
# Now Vs and ts have fixed length
print("Vs.shape: ", Vs.shape)
print("thetas.shape: ", thetas.shape)
print("fs.shape: ", fs.shape)
print("ts.shape: ", ts.shape)

Vs.shape:  torch.Size([1000, 500])
thetas.shape:  torch.Size([1000, 500])
fs.shape:  torch.Size([1000, 500])
ts.shape:  torch.Size([1000, 500])


In [6]:
# Calculate Xs
Xs = torch.zeros(Vs.shape)
Xs[:, 1:] = torch.cumulative_trapezoid(Xs, ts)
print("Xs.shape: ", Xs.shape)

Xs.shape:  torch.Size([1000, 500])


# Defining NNs, for $W (V, \xi)$ and $D (V, \xi, \dot{\xi})$

# Calculate $f = \partial W / \partial V$, $\xi_{n+1}$ such that $\partial D / \partial \dot{\xi} + \partial W / \partial \xi = 0$

In [7]:
# Define class for training and calculating f
# Optimizer Adams
import torch.optim as optim

class PotentialsFric:
    # Initialization of W and D
    def __init__(self, kwgsPot):
        self.dim_xi = kwgsPot["dim_xi"]
        self.NNs_W = kwgsPot["NNs_W"]
        self.NNs_D = kwgsPot["NNs_D"]
        self.W = PP(self.NNs_W, input_dim = 1 + self.dim_xi, output_dim = 1)
        # self.D = PP(self.NNs_D, input_dim = 1 + 2 * self.dim_xi, output_dim = 1)
        self.optim_W = optim.Adam(self.W.parameters(), lr=kwgsPot["learning_rate"])
        # self.optim_D = optim.Adam(self.D.parameters(), lr=0.001)
        
        # Device
        self.device = kwgsPot["device"]
        self.W.to(self.device)
        
    # Calculate f 
    def calf(self, x, t):
        # Initialize Vs
        batch_size = x.shape[0]
        time_steps = x.shape[1]
        # xis[:, :, :] = 1. 
        
        
        # Loop through time steps
        
        if self.dim_xi > 0:
            xi0 = torch.zeros([batch_size, self.dim_xi], requires_grad=True, device=self.device)
            
            # List of fs
            list_fs = []
            list_xis = [xi0]
            
            for idx in range(x.shape[1]):
                # f = \partial W / \partial V
                X_W = torch.concat([x[:, idx:idx + 1], list_xis[-1]], dim = 1).requires_grad_()
                # X_W.to(self.device)
                W = torch.sum(self.W(X_W))

                this_piece = torch.autograd.grad(outputs=W, inputs=X_W, create_graph=True)[0]
                list_fs.append(this_piece[:, 0:1])

                # Solve for \dot{\xi} + \partial W / \partial \xi = 0
                dWdXi = this_piece[:, 1:]

                # XiDot = -dWdXi
                if idx < x.shape[1] - 1:
                    xiNext = list_xis[-1] - dWdXi * (t[:, idx + 1:idx + 2] - t[:, idx:idx + 1]) 
                    list_xis.append(xiNext)
                    
                self.fs = torch.concat(list_fs, dim=1)
        else:
            X_W = x.clone().reshape([x.shape[0], x.shape[1], 1]).requires_grad_()
            # print(X_W)
            W = torch.sum(self.W(X_W))
            self.fs = torch.autograd.grad(outputs=W, inputs=X_W, create_graph=True)[0].reshape([x.shape[0], x.shape[1]])
            # print('self.fs.shape: ', self.fs.shape)
            
            

In [8]:
# Different Potentials with D correction
class PotentialsFricCorrection:
    # Initialization of W and D
    def __init__(self, kwgsPot):
        self.dim_xi = kwgsPot["dim_xi"]
        self.NNs_W = kwgsPot["NNs_W"]
        self.NNs_D = kwgsPot["NNs_D"]
        self.W = PP(self.NNs_W, input_dim = 1 + self.dim_xi, output_dim = 1)
        self.D = PP(self.NNs_D, input_dim = self.dim_xi, output_dim = self.dim_xi)
        self.optim_W = optim.Adam(self.W.parameters(), lr=kwgsPot["learning_rate"])
        self.optim_D = optim.Adam(self.D.parameters(), lr=kwgsPot["learning_rate_D"])
        
        # Device
        self.device = kwgsPot["device"]
        self.W.to(self.device)
        self.D.to(self.device)
        
    # Calculate f 
    def calf(self, x, t):
        # Initialize Vs
        batch_size = x.shape[0]
        time_steps = x.shape[1]
        # xis[:, :, :] = 1. 
        
        
        # Loop through time steps
        
        if self.dim_xi > 0:
            xi0 = torch.zeros([batch_size, self.dim_xi], requires_grad=True, device=self.device)
            
            # List of fs
            list_fs = []
            list_xis = [xi0]
            
            for idx in range(x.shape[1]):
                # f = \partial W / \partial V
                X_W = torch.concat([x[:, idx:idx + 1], list_xis[-1]], dim = 1).requires_grad_()
                # X_W.to(self.device)
                W = torch.sum(self.W(X_W))

                this_piece = torch.autograd.grad(outputs=W, inputs=X_W, create_graph=True)[0]
                list_fs.append(this_piece[:, 0:1])

                # Solve for \dot{\xi} + \partial W / \partial \xi = 0
                dWdXi = this_piece[:, 1:]

                # XiDot = -dWdXi
                if idx < x.shape[1] - 1:
                    xiNext = list_xis[-1] + self.D(-dWdXi) * (t[:, idx + 1:idx + 2] - t[:, idx:idx + 1])
                    list_xis.append(xiNext)
                    
                self.fs = torch.concat(list_fs, dim=1)
        else:
            X_W = x.clone().reshape([x.shape[0], x.shape[1], 1]).requires_grad_()
            # print(X_W)
            W = torch.sum(self.W(X_W))
            self.fs = torch.autograd.grad(outputs=W, inputs=X_W, create_graph=True)[0].reshape([x.shape[0], x.shape[1]])

# Define Loss function, training function, dataloaders

In [19]:
# Define loss functions given fs_targ, fs. 
def Loss(fs_targ, fs, ts, p = 2):
    err = torch.trapz(torch.abs(fs_targ - fs) ** p, ts, dim = 1) / torch.trapz(torch.abs(fs_targ) ** p, ts, dim = 1)
    err = torch.pow(err, 1. / p)
    return torch.sum(err)

# Training for one epoch
def train1Epoch(data_loader, loss_fn, myPot, p, update_weights=True):
    # Record of losses for each batch
    Losses = []
    device=myPot.device
    
    # Enumerate over data_loader
    for idx, (Xs, ts, fs_targ) in enumerate(data_loader):
        # Send shits to GPU
        Xs = Xs.to(device)
        ts = ts.to(device)
        fs_targ = fs_targ.to(device)
        
        # Refresh the optimizers
        myPot.optim_W.zero_grad()
        
        if hasattr(myPot, 'optim_D'):
            myPot.optim_D.zero_grad()
        
        ## DEBUG LINE CHECK DEVICES
        # print("Xs.device: ", Xs.device)
        # print("Xs[:, 0:1].device: ", Xs[:, 0:1].device)
        
        # Compute loss
        myPot.calf(Xs, ts)
        loss = loss_fn(fs_targ, myPot.fs, ts, p)
        Losses.append(loss)
        
        # Update the model parameters
        if update_weights:
            loss.backward()
            myPot.optim_W.step()
        
            if hasattr(myPot, 'optim_D'):
                myPot.optim_D.step()
        
        
    res = sum(Losses) / len(data_loader.dataset)
    print("Memory before del in train1Epoch: ")
    memory_stats()

    del Xs, ts, fs_targ, Losses
    torch.cuda.empty_cache()

    print("Memory after del in train1Epoch: ")
    memory_stats()
    return res



In [20]:
# Initialize dataloaders
AllData = TensorDataset(
    Xs, 
    ts, 
    fs
)

dataloader_kwargs = {'num_workers': 1, 'pin_memory': True} if torch.cuda.is_available() else {}
# train_loader = torch.utils.data.DataLoader(train_data, batch_size=batch_size, shuffle=True, **kwargs)

train_len = int(len(Vs) * 0.8)
test_len = len(Vs) - train_len
trainDataset, testDataset = torch.utils.data.random_split(AllData, [train_len, test_len])

# Make an optuna function

In [21]:
class OptunaObj:
    # Initialize
    def __init__(self, kwgs):
        self.dim_xi = kwgs['dim_xi']
        self.test_p = kwgs['test_p']
        self.test_batch_size = kwgs['test_batch_size']
        self.device = kwgs['device']
        self.training_dataset = kwgs['training_dataset']
        self.test_dataset = kwgs['test_dataset']
        
        
    # Define the objective
    def objective(self, trial):
        # Dump for un-saved interuptions
        joblib.dump(this_study, "./data/study_dim_xi_DLeg_" + str(self.dim_xi) + ".pkl")

        # Fixed parameters
        dim_xi = self.dim_xi
        NNs_D = []
        test_p = self.test_p
        test_batch_size = self.test_batch_size

        # Define NN for W
        W_layers = trial.suggest_int('W_layers', 2, 5)
        NNs_W = []
        for i in range(W_layers):
            this_W = 2 ** trial.suggest_int('W_layer_units_exponent_{}'.format(i), 4, 10)
            NNs_W.append(this_W)
            
        # Define NN for D
        D_layers = trial.suggest_int('D_layers', 2, 5)
        NNs_D = []
        for i in range(D_layers):
            this_D = 2 ** trial.suggest_int('D_layer_units_exponent_{}'.format(i), 4, 10)
            NNs_D.append(this_D)

        # Suggest learning rate
        learning_rate = 10 ** trial.suggest_float('log_learning_rate', -5., -1.)
        
        # Suggest learning rate for D
        learning_rate_D = 10 ** trial.suggest_float('log_learning_rate_D', -5., -1.)

        # Suggest batchsize
        training_batch_size = 2 ** trial.suggest_int('training_batch_size', 6, 12)

        # Suggest training p
        training_p = trial.suggest_int('training_p', 2, 8)

        # Suggest training epochs
        # training_epochs = 2 ** trial.suggest_int('training_epoch_exponents', 5, 9)
        training_epochs = 100

        params = {
            'dim_xi' : dim_xi, 
            'NNs_W' : NNs_W, 
            'NNs_D' : NNs_D, 
            'learning_rate' : learning_rate, 
            'learning_rate_D' : learning_rate_D, 
            'training_batch_size' : training_batch_size, 
            'training_p' : training_p, 
            'training_epochs' : training_epochs, 
            'device' : self.device,
        }
        
        
        # Set training dataloader
        training_batch_size = params['training_batch_size'] #1024
        trainDataLoader = DataLoader(
            self.training_dataset,
            batch_size = training_batch_size,
            shuffle = True,
        #    num_workers = 16,
            collate_fn = None,
            **dataloader_kwargs, 
        )

        # Set testing data loader
        testing_batch_size = self.test_batch_size # 256
        testDataLoader = DataLoader(
            self.test_dataset,
            batch_size = testing_batch_size,
            shuffle = True,
        #    num_workers = 16,
            collate_fn = None,
            **dataloader_kwargs, 
        )
        
        # Print out info
        print("-"*20, " Trial ", str(trial.number), " ", "-"*20, flush=True)
        st = time.time()
        print("Start timing: ")
        
        print("Parameters: ", flush=True)
        print(trial.params, flush=True)
        
        # Training
        myWD = PotentialsFricCorrection(params)
        for i in range(params['training_epochs']):
            avg_training_loss = train1Epoch(trainDataLoader, Loss, myWD, params['training_p'])
            
            if torch.isnan(avg_training_loss):
                break
            
            if i % 10 == 0:
                # avg_test_loss = train1Epoch(testDataLoader, Loss, myWD, self.test_p, update_weights=False)
                print("\t", "epoch ", str(i), "training error: ", str(avg_training_loss), flush=True)
        
        # Return objective value for optuna
        res = train1Epoch(testDataLoader, Loss, myWD, self.test_p, update_weights=False)
        print("Time for this trial: ", time.time() - st)
        # Release GPU memory
        del myWD
        gc.collect()
        torch.cuda.empty_cache()
        
        ## Print memory status
        print("Memory status after this trial: ")
        memory_stats()
        
        return res
            
            

In [22]:
# Do a parametric study over number of hidden parameters
dim_xis = [1, 2, 4]
studys = []

# Tune parameters for dim_xi = 4
OptKwgs = {
    'dim_xi' : 4, 
    'test_p' : 2, 
    'test_batch_size' : len(testDataset), 
    'device' : device, 
    'training_dataset' : trainDataset, 
    'test_dataset' : testDataset, 
}

# Loop through all dim_xis
for dim_xi in dim_xis:
    OptKwgs['dim_xi'] = dim_xi
    myOpt = OptunaObj(OptKwgs)
    this_study = optuna.create_study(direction='minimize')
    this_study.optimize(myOpt.objective, n_trials=50)
    studys.append(this_study)


[I 2023-10-26 22:05:02,998] A new study created in memory with name: no-name-9baa6280-af84-4488-b792-facfaaa9f199


--------------------  Trial  0   --------------------
Start timing: 
Parameters: 
{'W_layers': 2, 'W_layer_units_exponent_0': 8, 'W_layer_units_exponent_1': 4, 'D_layers': 5, 'D_layer_units_exponent_0': 9, 'D_layer_units_exponent_1': 9, 'D_layer_units_exponent_2': 6, 'D_layer_units_exponent_3': 9, 'D_layer_units_exponent_4': 9, 'log_learning_rate': -4.1183890496934845, 'log_learning_rate_D': -4.14126284747863, 'training_batch_size': 7, 'training_p': 8}
Memory before del in train1Epoch: 
Memory allocated:  1793.4306640625
Memory cached:  3252.0
Memory after del in train1Epoch: 
Memory allocated:  1793.24462890625
Memory cached:  1848.0
	 epoch  0 training error:  tensor(1.1323, device='cuda:0', grad_fn=<DivBackward0>)
Memory before del in train1Epoch: 
Memory allocated:  1793.43798828125
Memory cached:  3102.0
Memory after del in train1Epoch: 
Memory allocated:  1793.251953125
Memory cached:  1848.0
Memory before del in train1Epoch: 
Memory allocated:  1793.43798828125
Memory cached:  3

[I 2023-10-26 22:33:55,370] Trial 0 finished with value: 0.19846731424331665 and parameters: {'W_layers': 2, 'W_layer_units_exponent_0': 8, 'W_layer_units_exponent_1': 4, 'D_layers': 5, 'D_layer_units_exponent_0': 9, 'D_layer_units_exponent_1': 9, 'D_layer_units_exponent_2': 6, 'D_layer_units_exponent_3': 9, 'D_layer_units_exponent_4': 9, 'log_learning_rate': -4.1183890496934845, 'log_learning_rate_D': -4.14126284747863, 'training_batch_size': 7, 'training_p': 8}. Best is trial 0 with value: 0.19846731424331665.


Memory status after this trial: 
Memory allocated:  3809.00244140625
Memory cached:  3866.0
--------------------  Trial  1   --------------------
Start timing: 
Parameters: 
{'W_layers': 3, 'W_layer_units_exponent_0': 7, 'W_layer_units_exponent_1': 6, 'W_layer_units_exponent_2': 5, 'D_layers': 3, 'D_layer_units_exponent_0': 7, 'D_layer_units_exponent_1': 4, 'D_layer_units_exponent_2': 5, 'log_learning_rate': -4.912670568368801, 'log_learning_rate_D': -4.657566056967868, 'training_batch_size': 8, 'training_p': 4}
Memory before del in train1Epoch: 
Memory allocated:  1784.51904296875
Memory cached:  3866.0
Memory after del in train1Epoch: 
Memory allocated:  1784.33447265625
Memory cached:  1840.0
	 epoch  0 training error:  tensor(1.1148, device='cuda:0', grad_fn=<DivBackward0>)
Memory before del in train1Epoch: 
Memory allocated:  1784.5263671875
Memory cached:  2400.0
Memory after del in train1Epoch: 
Memory allocated:  1784.341796875
Memory cached:  1840.0
Memory before del in train1

[I 2023-10-26 22:50:33,140] Trial 1 finished with value: 0.20141993463039398 and parameters: {'W_layers': 3, 'W_layer_units_exponent_0': 7, 'W_layer_units_exponent_1': 6, 'W_layer_units_exponent_2': 5, 'D_layers': 3, 'D_layer_units_exponent_0': 7, 'D_layer_units_exponent_1': 4, 'D_layer_units_exponent_2': 5, 'log_learning_rate': -4.912670568368801, 'log_learning_rate_D': -4.657566056967868, 'training_batch_size': 8, 'training_p': 4}. Best is trial 0 with value: 0.19846731424331665.


...

Memory before del in train1Epoch: 
Memory allocated:  2155.87451171875
Memory cached:  2194.0
Memory after del in train1Epoch: 
Memory allocated:  2154.72900390625
Memory cached:  2172.0
Time for this trial:  311.61829113960266
Memory status after this trial: 
Memory allocated:  2154.27294921875
Memory cached:  2172.0
--------------------  Trial  9   --------------------
Start timing: 
Parameters: 
{'W_layers': 3, 'W_layer_units_exponent_0': 10, 'W_layer_units_exponent_1': 4, 'W_layer_units_exponent_2': 10, 'D_layers': 2, 'D_layer_units_exponent_0': 4, 'D_layer_units_exponent_1': 6, 'log_learning_rate': -4.193569945077803, 'log_learning_rate_D': -3.7606333138637114, 'training_batch_size': 6, 'training_p': 5}
Memory before del in train1Epoch: 
Memory allocated:  1784.931640625
Memory cached:  2696.0
Memory after del in train1Epoch: 
Memory allocated:  1784.74267578125
Memory cached:  1836.0
	 epoch  0 training error:  tensor(0.5834, device='cuda:0', grad_fn=<DivBackward0>)
Memory before

[I 2023-10-27 10:21:17,017] Trial 9 finished with value: 0.20227700471878052 and parameters: {'W_layers': 3, 'W_layer_units_exponent_0': 10, 'W_layer_units_exponent_1': 4, 'W_layer_units_exponent_2': 10, 'D_layers': 2, 'D_layer_units_exponent_0': 4, 'D_layer_units_exponent_1': 6, 'log_learning_rate': -4.193569945077803, 'log_learning_rate_D': -3.7606333138637114, 'training_batch_size': 6, 'training_p': 5}. Best is trial 5 with value: 0.1983865648508072.


Memory status after this trial: 
Memory allocated:  4608.14794921875
Memory cached:  5312.0
--------------------  Trial  10   --------------------
Start timing: 
Parameters: 
{'W_layers': 2, 'W_layer_units_exponent_0': 10, 'W_layer_units_exponent_1': 10, 'D_layers': 5, 'D_layer_units_exponent_0': 5, 'D_layer_units_exponent_1': 8, 'D_layer_units_exponent_2': 4, 'D_layer_units_exponent_3': 6, 'D_layer_units_exponent_4': 4, 'log_learning_rate': -3.7181322845738674, 'log_learning_rate_D': -3.8596771414035835, 'training_batch_size': 11, 'training_p': 6}


[W 2023-10-27 10:21:20,006] Trial 10 failed with parameters: {'W_layers': 2, 'W_layer_units_exponent_0': 10, 'W_layer_units_exponent_1': 10, 'D_layers': 5, 'D_layer_units_exponent_0': 5, 'D_layer_units_exponent_1': 8, 'D_layer_units_exponent_2': 4, 'D_layer_units_exponent_3': 6, 'D_layer_units_exponent_4': 4, 'log_learning_rate': -3.7181322845738674, 'log_learning_rate_D': -3.8596771414035835, 'training_batch_size': 11, 'training_p': 6} because of the following error: RuntimeError('CUDA out of memory. Tried to allocate 20.00 MiB (GPU 0; 15.73 GiB total capacity; 13.47 GiB already allocated; 64.12 MiB free; 14.20 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF').
Traceback (most recent call last):
  File "/home/shengduo/anaconda3/lib/python3.9/site-packages/optuna/study/_optimize.py", line 200, in _run_trial
    value_or_values = func(tri

RuntimeError: CUDA out of memory. Tried to allocate 20.00 MiB (GPU 0; 15.73 GiB total capacity; 13.47 GiB already allocated; 64.12 MiB free; 14.20 GiB reserved in total by PyTorch) If reserved memory is >> allocated memory try setting max_split_size_mb to avoid fragmentation.  See documentation for Memory Management and PYTORCH_CUDA_ALLOC_CONF

In [1]:
dim_xis = [1, 2, 4]
for idx, dim_xi in enumerate(dim_xis):
    print("-" * 20, " dim_xi = ", dim_xi, " ", "-" * 20)
    shit = joblib.load('./data/study_dim_xi_Dexp_{0}.pkl'.format(dim_xi))
    print("best_params: ", shit.best_params)
    print("best_value: ", shit.best_value)

--------------------  dim_xi =  1   --------------------


NameError: name 'joblib' is not defined

# Demo: Try taking gradients w.r.t. inputs, this works

In [38]:
memory_stats()

13429.31591796875
14524.0


/home/shengduo/anaconda3/lib/python3.9/site-packages/torch/cuda/memory.py:391: FutureWarning: torch.cuda.memory_cached has been renamed to torch.cuda.memory_reserved
  warnings.warn(


In [39]:
del this_study

13429.31591796875
14524.0


In [ ]:
OptKwgs['dim_xi'] = 8
myOpt = OptunaObj(OptKwgs)
this_study = optuna.create_study(direction='minimize')
this_study.optimize(myOpt.objective, n_trials=50)
studys.append(this_study)

[I 2023-10-20 10:32:48,058] A new study created in memory with name: no-name-1b7e167f-d716-46cc-b919-41be5be1dacf


--------------------  Trial  0   --------------------
Parameters: 
{'W_layers': 7, 'W_layer_units_exponent_0': 6, 'W_layer_units_exponent_1': 6, 'W_layer_units_exponent_2': 7, 'W_layer_units_exponent_3': 10, 'W_layer_units_exponent_4': 6, 'W_layer_units_exponent_5': 4, 'W_layer_units_exponent_6': 4, 'D_layers': 2, 'D_layer_units_exponent_0': 7, 'D_layer_units_exponent_1': 5, 'log_learning_rate': -2.1740270893419456, 'log_learning_rate_D': -1.8049883560485425, 'training_batch_size': 11, 'training_p': 2}
DXi:  tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], device='cuda:0', requires_grad=True)
DXi:  tensor([[ 0.1296,  0.1186, -0.0344,  ..., -0.0241, -0.0290, -0.0047],
        [ 0.1296,  0.1186, -0.0344,  ..., -0.0241, -0.0290, -0.0047],
        [ 0.1296,  0.1186, -0.0344,  ..., -0.0241

[W 2023-10-20 10:33:10,813] Trial 0 failed with parameters: {'W_layers': 7, 'W_layer_units_exponent_0': 6, 'W_layer_units_exponent_1': 6, 'W_layer_units_exponent_2': 7, 'W_layer_units_exponent_3': 10, 'W_layer_units_exponent_4': 6, 'W_layer_units_exponent_5': 4, 'W_layer_units_exponent_6': 4, 'D_layers': 2, 'D_layer_units_exponent_0': 7, 'D_layer_units_exponent_1': 5, 'log_learning_rate': -2.1740270893419456, 'log_learning_rate_D': -1.8049883560485425, 'training_batch_size': 11, 'training_p': 2} because of the following error: The value nan is not acceptable.
[W 2023-10-20 10:33:10,815] Trial 0 failed with value tensor(nan, device='cuda:0', grad_fn=<DivBackward0>).


--------------------  Trial  1   --------------------
Parameters: 
{'W_layers': 8, 'W_layer_units_exponent_0': 8, 'W_layer_units_exponent_1': 10, 'W_layer_units_exponent_2': 4, 'W_layer_units_exponent_3': 7, 'W_layer_units_exponent_4': 7, 'W_layer_units_exponent_5': 10, 'W_layer_units_exponent_6': 6, 'W_layer_units_exponent_7': 7, 'D_layers': 5, 'D_layer_units_exponent_0': 10, 'D_layer_units_exponent_1': 7, 'D_layer_units_exponent_2': 7, 'D_layer_units_exponent_3': 10, 'D_layer_units_exponent_4': 8, 'log_learning_rate': -3.297885589978985, 'log_learning_rate_D': -4.090366640652964, 'training_batch_size': 9, 'training_p': 6}
DXi:  tensor([[0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        ...,
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.],
        [0., 0., 0.,  ..., 0., 0., 0.]], device='cuda:0', requires_grad=True)
DXi:  tensor([[ 0.0571, -0.0092,  0.0313,  ...,  0.0476,  0.0631, -0.03

In [1]:
b = torch.tensor([[2],[1]])
b

NameError: name 'torch' is not defined

In [399]:
a / b

tensor([[-0.0381,  0.3545, -0.9407, -0.6392, -0.7341],
        [ 0.4466, -1.4642,  0.0669,  1.8598, -0.8693]])

In [3]:
# Construct my NN with initialized default parameters 
NNs = [16, 16]
input_dim = 4
output_dim = 1

myPP = PP(NNs, input_dim, output_dim)

In [23]:
# Try taking gradients w.r.t. the inputs
x = torch.tensor([[1., 2., -1., 3.]], requires_grad=True)
y = torch.sum(myPP(x))
dydx = torch.autograd.grad(outputs=y, inputs=x, retain_graph=True)[0]

# Show values and gradients
print("y: ", y)
print("dydx: ", dydx)

y:  tensor(-0.1882, grad_fn=<SumBackward0>)
dydx:  tensor([[ 0.0650, -0.0497, -0.0758, -0.0635]])


In [22]:
# Try taking gradients w.r.t. the inputs
x = torch.tensor([[1., 2., -1., 3.], [-1., -3., 2., 5.]], requires_grad=True)
y = torch.sum(myPP(x))
dydx = torch.autograd.grad(outputs=y, inputs=x, retain_graph=True)[0]

# Show values and gradients
print("y: ", y)
print("dydx: ", dydx)

y:  tensor(-0.3059, grad_fn=<SumBackward0>)
dydx:  tensor([[ 0.0650, -0.0497, -0.0758, -0.0635],
        [ 0.0623, -0.0945, -0.0193, -0.0369]])


In [20]:
dydx[0]

tensor([[ 0.0650, -0.0497, -0.0758, -0.0635],
        [ 0.0623, -0.0945, -0.0193, -0.0369]])

In [21]:
y

tensor(-0.3059, grad_fn=<SumBackward0>)